In [1]:
#get authorization from google drive
#from google.colab import drive
#drive.mount('/content/drive')

In [2]:
#load original record
#import glob
#File_path = "/Users/prajwal/Desktop/Columbia/C4SR/hnyc_cd_processing-master/input/1880/nypl_1880_clean_records.txt"
#with open(file_path) as f:
  #data = f.readlines()  

In [3]:
#load original record
#import glob
#file_path = "/Users/prajwal/Desktop/Columbia/C4SR/doubt/dump/doubt5 filter11.txt"
#with open(file_path) as f:
  #data = f.readlines()  

In [4]:
#data

In [5]:
"""
n = len(data)
full_entry = []
for i in range(n):
  ls = data[i].split()
  if ls:
    if ls[0][1:] != "***":
      full_entry.append(' '.join(ls))
"""

'\nn = len(data)\nfull_entry = []\nfor i in range(n):\n  ls = data[i].split()\n  if ls:\n    if ls[0][1:] != "***":\n      full_entry.append(\' \'.join(ls))\n'

In [6]:
#retrieve result
#import pickle
#with open("/Users/prajwal/Desktop/Columbia/C4SR/hnyc_cd_processing-master/input/1880/prediction.pkl", 'rb') as f:
  #d = pickle.load(f)

In [7]:
#retrieve result
import pickle
#with open("/Users/prajwal/Desktop/Columbia/C4SR/doubt/doubt6-filter11.pkl", 'rb') as f:
#with open('/Users/prajwal/Desktop/Columbia/C4SR/mn_1850/doubt-mn1850-v7.pkl', 'rb') as f:
#with open('/Users/prajwal/Desktop/Columbia/C4SR/tesseract output/run1/mn-1880-3.pkl', 'rb') as f:
with open('/Users/prajwal/Desktop/Columbia/C4SR/tesseract lib/mn 1850/data/mn-1850-3.pkl', 'rb') as f:
  d = pickle.load(f)

In [8]:
n = len(d)

In [9]:
n

80569

##Extract different components from prediction results

Only extract information that we need and ignore delimiters.

In [10]:
output = []
for record in d:
    d_record = {}
    try:
        d_record["index"] = int(record[0])
        n = len(record[1])
        start = 1
        for i in range(1, n + 1):
            if i <  n:
              #skip delimiters
              if record[2][i] == "D":
                start = i+1
                continue
              elif record[2][i+1] == "D":
                try:
                  d_record[record[2][i]].append(record[1][(start-1):i])
                except:
                  d_record[record[2][i]] = [record[1][(start-1):i]]
                start = i + 2
            else:
              try:
                  d_record[record[2][i]].append(record[1][(start-1):])
              except:
                  d_record[record[2][i]] = [record[1][(start-1):]]

        output.append(d_record)
    except:
        pass

Further organize prediction results. 

In [11]:
agg = {}
for record in output:
  new = {}

  try:
    occupation = record['OC']
    new['Occupation'] = []
    for oc in occupation:
      new['Occupation'].append(' '.join(oc))
    new['Occupation'] = ' '.join(new['Occupation'])
  except:
    pass

  try:
    #deal with widow marriage status
    new['Name'] = []
    names = record['NC']
    for name in names:
      name_new = name[0]
      n = len(name)
      for i in range(1,n):
        if name[i] == '.':
          name_new += name[i]
        else:
          name_new += ' '
          name_new += name[i]
      new['Name'].append(name_new)
  
  except:
    pass

  try:
    #multiple address
    new['Address'] = []
    addresses = record['AC']
    for address in addresses:
      address_new = address[0]
      n = len(address)
      for i in range(1,n):
        if address[i] == '.':
          address_new += address[i]
        else:
          address_new += ' '
          address_new += address[i]
      new['Address'].append(address_new)

  except:
    pass
  
  agg[str(record['index'])] = new

In [12]:
#n = len(full_entry)
n = len(d)
final_output = {}
#generate fields
#for i in range(1,n+1):
for i in range(0,n):
    cd = {}
    cd['address'] = ''
    #full_entry_ls = full_entry[i-1].split()
    #cd['Index'] = full_entry_ls[0]
    #cd['Full Entry'] = ' '.join(full_entry_ls[1:])
    try:
        record = agg[str(i)]

        try:
            address = record['Address']
            for i in range(len(address)-1):
              h_add = address[i]
              h_add_1 = h_add.split()
              if ((h_add_1[0] in ('h','h.','w','w.','W','W.')) or (h_add_1[0].isdigit()) or (h_add_1[1].isdigit()) or (h_add_1[2].isdigit())):
                continue
              else:
                cd['address'] = ','.join(address[i])

        except:
            pass

        final_output[str(i)] = cd
    except:
        pass

In [13]:
len(final_output)

80569

#Generate final fields

Come up with a list of cities.

In [14]:
cities = ['Hoboken', 'N. J.', 'Spain', 'B’klyn', 'Mt. Vernon','Brooklyn','Jersey City']
def has_city(address, cities = cities):
  for city in cities:
    if city in address:
      return city
  return ''

For address, if there is a house number then further extract street name and city. If not, assume the address is a city name.

Notice that sometimes house number is not always at the beginning of the address. Example: h r 504 W. 55th

In [15]:
#n = len(full_entry)
n = len(d)
final_output = {}
#generate fields
#for i in range(1,n+1):
for i in range(0,n):
  try:
    print(i, agg[str(i)])
  except:
    agg[str(i)] = ''
  cd = {}
  cd['Full Name'] = ''
  cd['First Name'] = ''
  cd['Last Name'] = ''
  cd['Middle Name'] = ''
  cd['Widow-flag'] = 'False'
  cd['Widow Of'] = ''
  cd['Title'] = ''
  cd['Occupation'] = ''
  cd['Full Address'] = ''
  cd['H Status-flag'] = ''
  cd['H Address'] = ''
  cd['H House Number'] = ''
  cd['H Street Name'] = ''
  cd['H City'] = ''
  cd['Address 2'] = ''
  cd['Address 2 House Number'] = ''
  cd['Address 2 Street Name'] = ''
  cd['Address 2 City'] = ''
  #full_entry_ls = full_entry[i-1].split()
  #cd['Index'] = full_entry_ls[0]
  #cd['Full Entry'] = ' '.join(full_entry_ls[1:])

  try:
      record = agg[str(i)]
  
      #name
      try:
        name = record['Name']
        cd['Full Name'] = name[0]
        name_ls = name[0].split()
        if len(name_ls) == 2:
          cd['Last Name'] = name_ls[0]
          cd['First Name'] = name_ls[1]
        elif len(name_ls) == 3:
          cd['Last Name'] = name_ls[0]
          cd['First Name'] = name_ls[1]
          cd['Middle Name'] = name_ls[2]

        #widow flag
        if len(name) == 2:
          name_ls2 = name[1].split()
          if name_ls2[0] == 'widow' or 'wid.':
            cd['Widow-flag'] = 'True'
          if len(name_ls2) > 1:
            cd['Widow Of'] = ' '.join(name_ls2[1:])
      except:
        pass

      #occupation
      try:
        cd['Occupation'] = record['Occupation']
      except:
        pass

      #address
      try:
        address = record['Address']
        cd['Full Address'] = ','.join(address)
        if len(address) == 1:
          cd['H Address'] = address[0]
          address_1 = address[0].split()
          if ((address_1[0] == 'h') or (address_1[0] == 'h.')):
            cd['H Status-flag'] = 'True'
            start = 1
          else:
            cd['H Status-flag'] = 'Assume'
            start = 0

          house_num = False
          if address_1[start].isdigit():
            house_num = True
          elif address_1[start+1].isdigit():
            house_num = True
            start += 1

          if house_num:
            cd['H House Number'] = address_1[start]
            #city
            city = has_city(cities, address_1)
            if city:
              cd['H City'] = city
              cd['H Street Name'] = ' '.join(address_1[(start+1):]).replace(city,'').strip()
            else:
              cd['H Street Name'] = ' '.join(address_1[(start+1):])
          else:
            cd['H City'] = ' '.join(address_1[start:])

        else:
          add = address[0]
          add_ls = add.split()
          cd['Address 2'] = add
          start = 0
          house_num = False
          if add_ls[start].isdigit():
            house_num = True
          elif add_ls[start+1].isdigit():
            house_num = True
            start += 1
          if house_num:
            cd['Address 2 House Number'] = add_ls[start]
            #city
            city = has_city(add)
            if city:
              cd['Address 2 City'] = city
              cd['Address 2 Street Name'] = ' '.join(add_ls[(start+1):]).replace(city, '').strip()
            else:
              cd['Address 2 Street Name'] = ' '.join(add_ls[(start+1):])
          else:
            cd['Address 2 City'] = ' '.join(add_ls[start:])

          add_1 = address[1]
          add_ls = add_1.split()
          if ((add_ls[0] == 'h') or (add_ls[0] == 'h.')):
            cd['H Address'] = add_1
            cd['H Status-flag'] = 'True'
            start = 1
            house_num = False
            if add_ls[start].isdigit():
              house_num = True
            elif add_ls[start+1].isdigit():
              house_num = True
              start += 1
            if house_num:
              cd['H House Number'] = add_ls[start]
              #city
              city = has_city(add_1)
              if city:
                cd['H City'] = city
                cd['H Street Name'] = ' '.join(add_ls[(start+1):]).replace(city, '').strip()
              else:
                cd['H Street Name'] = ' '.join(add_ls[(start+1):])
            else:
              cd['H City'] = ' '.join(add_ls[start:])

      except:
        pass

  except:
      #break
      continue

  final_output[str(i)] = cd

0 {'Name': [], 'Address': ['39 Pearl']}
1 {'Name': [], 'Address': ['170 Clinton Brooklyn']}
2 {'Name': [], 'Address': ['601 Washington']}
3 {'Name': [], 'Address': ['328 Bowery']}
4 {'Name': [], 'Address': ['42 Orange']}
5 {'Name': [], 'Address': ['77 Barrow']}
6 {'Name': [], 'Address': ['586 E 4th']}
7 {'Name': [], 'Address': ['34 Av C']}
8 {'Name': [], 'Address': ['34 Av C']}
9 {'Name': [], 'Address': ['40 Av C']}
10 {'Name': [], 'Address': ['175 Canal']}
11 {'Name': [], 'Address': ['137 Norfolk']}
12 {'Name': [], 'Address': ['53 Av D']}
13 {'Name': [], 'Address': ['5 Ludlow']}
14 {'Name': [], 'Address': ['1 Av D']}
15 {'Name': [], 'Address': ['Morrisania']}
16 {'Name': [], 'Address': ['7 Murray']}
17 {'Name': [], 'Address': ['192 Fulton']}
18 {'Name': [], 'Address': ['91 Henry Brooklyn']}
19 {'Name': [], 'Address': ['181 inventor']}
20 {'Name': [], 'Address': ['79 Av B']}
21 {'Name': [], 'Address': ['66 Mangin']}
22 {'Name': [], 'Address': ['304 Ninth']}
23 {'Name': [], 'Address': [

950 {'Name': [], 'Address': ['33 Canal']}
951 {'Name': [], 'Address': ['504 Hudson']}
952 {'Name': [], 'Address': ['248 Rivington']}
953 {'Name': [], 'Address': ['523 Hdsn 15 Morton']}
954 {'Name': [], 'Address': ['214 Broome']}
955 {'Name': [], 'Address': ['636 Greenwich']}
956 {'Name': [], 'Address': ['Wmsburg']}
957 {'Name': [], 'Address': ['266 Monroe']}
958 {'Name': [], 'Address': ['10 Morton']}
959 {'Name': [], 'Address': ['169 Henry']}
960 {'Name': [], 'Address': ['164 Christopher']}
961 {'Name': [], 'Address': ['534 Hudson']}
962 {'Name': [], 'Address': ['Wmsbg Cherry']}
963 {'Name': [], 'Address': ['203 W 24th']}
964 {'Name': [], 'Address': ['161 Mott']}
965 {'Name': [], 'Address': ['22 Morton']}
966 {'Name': [], 'Address': ['468 Houston']}
967 {'Name': [], 'Address': ['22 Morton']}
968 {'Name': [], 'Address': ['262 Seventh']}
969 {'Name': [], 'Address': ['61 Leroy']}
970 {'Name': [], 'Address': ['419 Broadway 93 Morton']}
971 {'Name': [], 'Address': ['44 Broome']}
972 {'Name'

1700 {'Name': [], 'Address': ['49 E 16th']}
1701 {'Name': [], 'Address': ['82 Sheriff']}
1702 {'Name': [], 'Address': ['79 Av B']}
1703 {'Name': [], 'Address': ['Jersey city']}
1704 {'Name': [], 'Address': ['117 Ludlow']}
1705 {'Name': [], 'Address': ['112 Wm']}
1706 {'Name': [], 'Address': ['10 Rose 10 Rose']}
1707 {'Name': [], 'Address': ['647 Greenwich']}
1708 {'Name': [], 'Address': ['G wich']}
1709 {'Name': [], 'Address': ['59 West']}
1710 {'Name': [], 'Address': ['562 Fourth']}
1711 {'Name': [], 'Address': ['158 Stantn']}
1712 {'Name': [], 'Address': ['156 Stanton']}
1713 {'Name': [], 'Address': ['162 Suffolk']}
1714 {'Name': [], 'Address': ['62 Canal']}
1715 {'Name': [], 'Address': ['66 White']}
1716 {'Name': [], 'Address': ['21 Clinton']}
1717 {'Name': [], 'Address': ['E 25th h Av 1 & 2']}
1718 {'Name': [], 'Address': ['230 Tenth']}
1719 {'Name': [], 'Address': ['250 Seventh']}
1720 {'Name': [], 'Address': ['38 Pierpont Brooklyn']}
1721 {'Name': [], 'Address': ['73 Cranberry Br

2450 {'Name': [], 'Address': ['71 Stanton']}
2451 {'Name': [], 'Address': ['131 Broome']}
2452 {'Name': [], 'Address': ['59 Orchard']}
2453 {'Name': [], 'Address': ['W 28th n Av 6']}
2454 {'Name': [], 'Address': ['Av 2 n E 28th']}
2455 {'Name': [], 'Address': ['W 28th n Av 7']}
2456 {'Name': [], 'Address': ['109 W 20th']}
2457 {'Name': [], 'Address': ['198 Mott']}
2458 {'Name': [], 'Address': ['39 Wooster']}
2459 {'Name': [], 'Address': ['Morrisania']}
2460 {'Name': [], 'Address': ['189 Grand']}
2461 {'Name': [], 'Address': ['212 Broadway']}
2462 {'Name': [], 'Address': ['60 Morton']}
2463 {'Name': [], 'Address': ['602 Grand']}
2464 {'Name': [], 'Address': ['106 W 24th']}
2465 {'Name': [], 'Address': ['Brooklyn']}
2466 {'Name': [], 'Address': ['E 26th c Av 4']}
2467 {'Name': [], 'Address': ['Av 4']}
2468 {'Name': [], 'Address': ['158 Norfolk']}
2469 {'Name': [], 'Address': ['79 Hudson']}
2470 {'Name': [], 'Address': ['60 Marion']}
2471 {'Name': [], 'Address': ['186 Av 9']}
2472 {'Name'

3199 {'Name': [], 'Address': ['41 Douglas Brooklyn']}
3200 {'Name': [], 'Address': ['Canada']}
3201 {'Name': [], 'Address': ['103 Mai']}
3202 {'Name': [], 'Address': ['76 Adams Brooklyn']}
3203 {'Name': ['Adelphio n De Kalb Avenue Brooklyn'], 'Address': []}
3204 {'Name': [], 'Address': ['3 Patchin place']}
3205 {'Name': [], 'Address': ['11 Cherry']}
3206 {'Name': [], 'Address': ['Av 8 un W 28th']}
3207 {'Name': [], 'Address': ['205 Front']}
3208 {'Name': [], 'Address': ['123 W 19th']}
3209 {'Name': [], 'Address': ['125 Ludlow']}
3210 {'Name': [], 'Address': ['187 Henry']}
3211 {'Name': [], 'Address': ['276 Ninth']}
3212 {'Name': [], 'Address': ['195 E Bway']}
3213 {'Name': [], 'Address': ['60 Wall 229 B way']}
3214 {'Name': [], 'Address': ['W 37th n Av 9']}
3215 {'Name': [], 'Address': ['86 W 16th']}
3216 {'Name': [], 'Address': ['79 King']}
3217 {'Name': [], 'Address': ['5334 Amos']}
3218 {'Name': [], 'Address': ['5312 Amos']}
3219 {'Name': [], 'Address': ['28 Lewis']}
3220 {'Name': [

...

76963 {'Name': [], 'Address': ['lridge']}
76964 {'Name': [], 'Address': ['Chrystie']}
76965 {'Name': [], 'Address': ['Brooklyn']}
76966 {'Name': [], 'Address': ['John']}
76967 {'Name': [], 'Address': ['Bleecker']}
76968 {'Name': [], 'Address': []}
76969 {'Name': [], 'Address': ['Williamsburg']}
76970 {'Name': [], 'Address': ['Charlton']}
76971 {'Name': [], 'Address': ['Brooklyn']}
76972 {'Name': [], 'Address': ['Charlton']}
76973 {'Name': [], 'Address': []}
76974 {'Name': [], 'Address': ['195 William']}
76975 {'Name': [], 'Address': ['24th']}
76976 {'Name': [], 'Address': []}
76977 {'Name': [], 'Address': ['10 c W 31st']}
76978 {'Name': [], 'Address': []}
76979 {'Name': [], 'Address': ['Greenwich ae']}
76980 {'Name': [], 'Address': []}
76981 {'Name': [], 'Address': []}
76982 {'Name': ['Tompkins'], 'Address': []}
76983 {'Name': [], 'Address': []}
76984 {'Name': [], 'Address': []}
76985 {'Name': [], 'Address': ['399 Greenwich']}
76986 {'Name': [], 'Address': ['Washington sq']}
76987 {'Na

77926 {'Name': [], 'Address': []}
77927 {'Name': [], 'Address': ['Houston']}
77928 {'Name': [], 'Address': ['22d n Av 3']}
77929 {'Name': [], 'Address': ['Division']}
77930 {'Name': [], 'Address': ['Av 3']}
77931 {'Name': [], 'Address': []}
77932 {'Name': [], 'Address': ['40 Thomas']}
77933 {'Name': [], 'Address': []}
77934 {'Name': [], 'Address': ['Twelfth']}
77935 {'Name': [], 'Address': ['19 North Moore']}
77936 {'Name': [], 'Address': ['Macdougal']}
77937 {'Name': [], 'Address': ['Commerce']}
77938 {'Name': [], 'Address': []}
77939 {'Name': [], 'Address': ['30th n Av 7']}
77940 {'Name': [], 'Address': ['Franklin']}
77941 {'Name': [], 'Address': ['44 Franklin']}
77942 {'Name': [], 'Address': ['Beaver']}
77943 {'Name': [], 'Address': ['Washington place as']}
77944 {'Name': [], 'Address': []}
77945 {'Name': [], 'Address': ['HER 235 HES']}
77946 {'Name': [], 'Address': ['31 Grove']}
77947 {'Name': [], 'Address': ['Division']}
77948 {'Name': [], 'Address': ['Division']}
77949 {'Name': [

78691 {'Name': [], 'Address': ['MAT']}
78692 {'Name': [], 'Address': ['ington']}
78693 {'Name': [], 'Address': ['9 EE 20th']}
78694 {'Name': [], 'Address': ['Hamilton']}
78695 {'Name': [], 'Address': ['Brooklyn']}
78696 {'Name': [], 'Address': ['berry']}
78697 {'Name': [], 'Address': ['Madison']}
78698 {'Name': [], 'Address': ['Sheriff']}
78699 {'Name': [], 'Address': ['Division']}
78700 {'Name': [], 'Address': ['Henry']}
78701 {'Name': [], 'Address': ['Vandam 21']}
78702 {'Name': [], 'Address': []}
78703 {'Name': [], 'Address': ['we as']}
78704 {'Name': [], 'Address': []}
78705 {'Name': [], 'Address': ['ore']}
78706 {'Name': [], 'Address': ['rsyth']}
78707 {'Name': [], 'Address': ['ladison']}
78708 {'Name': [], 'Address': ['22 Washington']}
78709 {'Name': [], 'Address': []}
78710 {'Name': [], 'Address': ['373 Bower']}
78711 {'Name': [], 'Address': []}
78712 {'Name': [], 'Address': ['Carmine']}
78713 {'Name': [], 'Address': ['Av']}
78714 {'Name': [], 'Address': ['77 Av 10']}
78715 {'Na

79506 {'Name': [], 'Address': []}
79507 {'Name': [], 'Address': ['38th n Av 6']}
79508 {'Name': [], 'Address': ['SIM 459 SIM']}
79509 {'Name': [], 'Address': ['22 Lispenard']}
79510 {'Name': [], 'Address': []}
79511 {'Name': [], 'Address': ['18 Spruce']}
79512 {'Name': [], 'Address': ['Brooklyn']}
79513 {'Name': [], 'Address': ['Tenth']}
79514 {'Name': [], 'Address': ['Hester']}
79515 {'Name': [], 'Address': ['Grand']}
79516 {'Name': [], 'Address': ['161 Barrow']}
79517 {'Name': [], 'Address': []}
79518 {'Name': [], 'Address': []}
79519 {'Name': [], 'Address': ['OKI']}
79520 {'Name': [], 'Address': []}
79521 {'Name': [], 'Address': ['Second']}
79522 {'Name': [], 'Address': ['Bowery']}
79523 {'Name': [], 'Address': []}
79524 {'Name': [], 'Address': ['Rathburn s hotel uo']}
79525 {'Name': [], 'Address': ['Wooster']}
79526 {'Name': [], 'Address': ['22 E 20th']}
79527 {'Name': [], 'Address': ['Clinton place']}
79528 {'Name': [], 'Address': []}
79529 {'Name': [], 'Address': ['45 Renwick']}


80307 {'Name': [], 'Address': ['Fr']}
80308 {'Name': [], 'Address': ['ZIL']}
80309 {'Name': ['Laurens'], 'Address': []}
80310 {'Name': [], 'Address': ['Murray']}
80311 {'Name': [], 'Address': ['Leonard']}
80312 {'Name': [], 'Address': ['135 Eighth']}
80313 {'Name': [], 'Address': ['Houston']}
80314 {'Name': [], 'Address': ['Madison']}
80315 {'Name': ['Ludlow'], 'Address': []}
80316 {'Name': [], 'Address': ['Broome']}
80317 {'Name': [], 'Address': ['ZWI']}
80318 {'Name': [], 'Address': ['5 Dey']}
80319 {'Name': [], 'Address': ['431 Washington']}
80320 {'Name': [], 'Address': ['Brooklyn']}
80321 {'Name': [], 'Address': ['CAR 93 CAR']}
80322 {'Name': [], 'Address': ['30th n Av 5 Carrigan Edward 24 Clif']}
80323 {'Name': [], 'Address': ['22 Rutgers']}
80324 {'Name': [], 'Address': ['liamsburg']}
80325 {'Name': [], 'Address': ['111 Front']}
80326 {'Name': [], 'Address': ['6 n W 30th']}
80327 {'Name': [], 'Address': ['vol']}
80328 {'Name': [], 'Address': ['CAS']}
80329 {'Name': [], 'Address'

In [16]:
len(final_output)

80569

In [17]:
#save final output
#import json
#with open('/Users/prajwal/Desktop/Columbia/C4SR/doubt/doubt5 filter11-2.json', 'w') as f:
    #json.dump(final_output,f)
#f.close()

In [18]:
import pandas as pd
final_output_df = pd.DataFrame(final_output).T

# Save pandas dataframe as pickle object
#with open("/Users/prajwal/Desktop/Columbia/C4SR/doubt/doubt5 filter11-2.pkl", 'wb') as f:
    #pickle.dump(final_output_df, f)

# Save to csv
#final_output_df.to_csv('/Users/prajwal/Desktop/Columbia/C4SR/doubt/doubt6-filter11.csv')
#final_output_df.to_csv('/Users/prajwal/Desktop/Columbia/C4SR/mn_1850/doubt-mn1850-v7 new.csv')
final_output_df.to_csv('/Users/prajwal/Desktop/Columbia/C4SR/tesseract lib/mn 1850/data/mn-1850-3.csv')

In [19]:
len(final_output_df)

80569